In [ ]:
!pip install -q -U bitsandbytes
!pip install transformers==4.31
!pip install -q -U git+https://github.com/huggingface/peft.git
!pip install -q -U git+https://github.com/huggingface/accelerate.git
!pip install -q datasets
!pip install evaluate
!pip install -qqq trl==0.7.1

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.6/92.6 MB 11.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.4/7.4 MB 19.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 58.0 MB/s eta 0:00:00
  Attempting uninstall: tokenizers
    Found existing installation: tokenizers 0.15.0
    Uninstalling tokenizers-0.15.0:
      Successfully uninstalled tokenizers-0.15.0
  Attempting uninstall: transformers
    Found existing installation: transformers 4.35.2
    Uninstalling transformers-4.35.2:
      Successfully uninstalled transformers-4.35.2
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 265.7/265.7 kB 4.7 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 521.2/521.2 k

In [ ]:
from datasets import load_dataset
checkpoint = 'knkarthick/dialogsum'

df = load_dataset(checkpoint)

Extracting data files:   0%|          | 0/3 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

In [ ]:
def get_prompt(dialogue: str, summary: str):
  return f"""###Instruction:
  Summarize the following dialogue

  Dialogue:
  {dialogue.strip()}

  Summary:
  {summary.strip()}
  """.strip()


In [ ]:
def generate_prompt_dataset(df):
  return {
      'dialogue': df['dialogue'],
      'summary': df['summary'],
      'text': get_prompt(df['dialogue'], df['summary'])
  }

In [ ]:
def prepare_dataset(data):
  return (
    data.shuffle(seed=42)
        .map(generate_prompt_dataset).remove_columns(['id', 'topic',])
  )

In [ ]:
# from torch.utils.data import DataLoader
# train_loader = DataLoader(train_dataset,batch_size=32,num_workers=4,pin_memory=True, shuffle=True)
# eval_loader = DataLoader(eval_dataset,batch_size=32,num_workers=4,pin_memory=True, shuffle=True)

In [ ]:
import torch
device = torch.device('cuda:0')

In [ ]:
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig

bnb =  BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16
)


In [ ]:


model = AutoModelForCausalLM.from_pretrained("NousResearch/Llama-2-7b-hf", quantization_config=bnb, device_map='auto', use_auth_token='add-your-token', )

tokenizer = AutoTokenizer.from_pretrained("NousResearch/Llama-2-7b-hf", use_auth_token='add-your-token')
tokenizer.pad_token= tokenizer.eos_token
tokenizer.padding_side = 'right'

config.json:   0%|          | 0.00/583 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/modeling_utils.py:2193: FutureWarning: The `use_auth_token` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


model.safetensors.index.json:   0%|          | 0.00/26.8k [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/9.98G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/3.50G [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/746 [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1714: FutureWarning: The `use_auth_token` argument is deprecated and will be removed in v5 of Transformers.
  warnings.warn(


tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.84M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/435 [00:00<?, ?B/s]

In [ ]:
model.named_parameters

<bound method Module.named_parameters of LlamaForCausalLM(
  (model): LlamaModel(
    (embed_tokens): Embedding(32000, 4096, padding_idx=0)
    (layers): ModuleList(
      (0-31): 32 x LlamaDecoderLayer(
        (self_attn): LlamaAttention(
          (q_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (k_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (v_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (o_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (rotary_emb): LlamaRotaryEmbedding()
        )
        (mlp): LlamaMLP(
          (gate_proj): Linear4bit(in_features=4096, out_features=11008, bias=False)
          (up_proj): Linear4bit(in_features=4096, out_features=11008, bias=False)
          (down_proj): Linear4bit(in_features=11008, out_features=4096, bias=False)
          (act_fn): SiLUActivation()
        )
        (input_layernorm): LlamaRMSNorm()
        (post_atte

In [ ]:
def print_params(model):
  trainable_params = 0
  all_params = 0
  for _, param in model.named_parameters():
    all_params+=param.numel()
    if param.requires_grad:
      trainable_params+=param.numel()

  print(
        f"trainable params: {trainable_params} || all params: {all_params} || trainable%: {100 * trainable_params / all_params}"
 )


In [ ]:
from peft import prepare_model_for_kbit_training

model.gradient_checkpointing_enable()
model = prepare_model_for_kbit_training(model)

In [ ]:
model

LlamaForCausalLM(
  (model): LlamaModel(
    (embed_tokens): Embedding(32000, 4096, padding_idx=0)
    (layers): ModuleList(
      (0-31): 32 x LlamaDecoderLayer(
        (self_attn): LlamaAttention(
          (q_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (k_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (v_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (o_proj): Linear4bit(in_features=4096, out_features=4096, bias=False)
          (rotary_emb): LlamaRotaryEmbedding()
        )
        (mlp): LlamaMLP(
          (gate_proj): Linear4bit(in_features=4096, out_features=11008, bias=False)
          (up_proj): Linear4bit(in_features=4096, out_features=11008, bias=False)
          (down_proj): Linear4bit(in_features=11008, out_features=4096, bias=False)
          (act_fn): SiLUActivation()
        )
        (input_layernorm): LlamaRMSNorm()
        (post_attention_layernorm): LlamaRMSNorm()
      )


In [ ]:
from peft import LoraConfig, get_peft_model

lora_config = LoraConfig(
    r=16,
    lora_alpha = 64,
    target_modules=['q_proj', 'k_proj', 'v_proj', 'o_proj'],
    bias='none',
    lora_dropout=0.1,
    task_type='CASUAL_LM'
)
# model.add_adapter(lora_config)

model = get_peft_model(model, lora_config)
print_params(model)

trainable params: 16777216 || all params: 3517190144 || trainable%: 0.477006226934315


In [ ]:
OUTPUT_DIR = "llama2-docsum-adapter"

In [ ]:
from transformers import TrainingArguments

training_arguments = TrainingArguments(
    per_device_train_batch_size=4,
    gradient_accumulation_steps=4,
    optim='paged_adamw_32bit',
    logging_steps=1,
    learning_rate=1e-4,
    fp16=True,
    max_grad_norm=0.3,
    num_train_epochs=3,
    evaluation_strategy='steps',
    eval_steps=0.2,
    warmup_ratio=0.05,
    output_dir=OUTPUT_DIR,
    report_to='none',
    save_safetensors=True,
    lr_scheduler_type='cosine',
    seed=42,
    remove_unused_columns=False
)
model.config.use_cache=False

In [ ]:
df['train']

Dataset({
    features: ['id', 'dialogue', 'summary', 'topic'],
    num_rows: 12460
})

In [ ]:
df['train']= prepare_dataset(df['train'])
df['validation']= prepare_dataset(df['validation'])
df['test']= prepare_dataset(df['test'])
train_data = df['train'].shuffle(seed=42).select([i for i in range(500)])
test_data = df['test'].shuffle(seed=42).select([i for i in range(50)])
validation_data = df['validation'].shuffle(seed=42).select([i for i in range(50)])

train_data,test_data,validation_data


Map:   0%|          | 0/12460 [00:00<?, ? examples/s]

Map:   0%|          | 0/500 [00:00<?, ? examples/s]

Map:   0%|          | 0/1500 [00:00<?, ? examples/s]

(Dataset({
     features: ['dialogue', 'summary', 'text'],
     num_rows: 500
 }),
 Dataset({
     features: ['dialogue', 'summary', 'text'],
     num_rows: 50
 }),
 Dataset({
     features: ['dialogue', 'summary', 'text'],
     num_rows: 50
 }))

In [ ]:
df

DatasetDict({
    train: Dataset({
        features: ['dialogue', 'summary', 'text'],
        num_rows: 12460
    })
    validation: Dataset({
        features: ['dialogue', 'summary', 'text'],
        num_rows: 500
    })
    test: Dataset({
        features: ['dialogue', 'summary', 'text'],
        num_rows: 1500
    })
})

In [ ]:
from trl import SFTTrainer

trainer = SFTTrainer(
    model=model,
    train_dataset=train_data,
    eval_dataset=validation_data,
    peft_config=lora_config,
    dataset_text_field='text',
    max_seq_length=1024,
    tokenizer=tokenizer,
    args=training_arguments
)

trainer.train()

Map:   0%|          | 0/500 [00:00<?, ? examples/s]

Map:   0%|          | 0/50 [00:00<?, ? examples/s]

You're using a LlamaTokenizerFast tokenizer. Please note that with a fast tokenizer, using the `__call__` method is faster than using a method to encode the text followed by a call to the `pad` method to get a padded encoding.
/usr/local/lib/python3.10/dist-packages/torch/utils/checkpoint.py:429: UserWarning: torch.utils.checkpoint: please pass in use_reentrant=True or use_reentrant=False explicitly. The default value of use_reentrant will be updated to be False in the future. To maintain current behavior, pass use_reentrant=True. It is recommended that you use use_reentrant=False. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


TrainOutput(global_step=93, training_loss=1.264249195334732, metrics={'train_runtime': 2513.5877, 'train_samples_per_second': 0.597, 'train_steps_per_second': 0.037, 'total_flos': 1.2725736297725952e+16, 'train_loss': 1.264249195334732, 'epoch': 2.98})

In [ ]:
peft_model_path="./llama-dialogue-summarizer"

trainer.model.save_pretrained(peft_model_path)
tokenizer.save_pretrained(peft_model_path)

('./llama-dialogue-summarizer/tokenizer_config.json',
 './llama-dialogue-summarizer/special_tokens_map.json',
 './llama-dialogue-summarizer/tokenizer.json')

In [ ]:
!pip install huggingface_hub

In [ ]:
!huggingface-cli login --token 'add-your-token'

Token will not been saved to git credential helper. Pass `add_to_git_credential=True` if you want to set the git credential as well.
Token is valid (permission: write).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [ ]:
!zip -r llama-dialogue-summarizer.zip /content/llama-dialogue-summarizer

  adding: content/llama-dialogue-summarizer/ (stored 0%)
  adding: content/llama-dialogue-summarizer/tokenizer.json (deflated 74%)
  adding: content/llama-dialogue-summarizer/special_tokens_map.json (deflated 72%)
  adding: content/llama-dialogue-summarizer/adapter_model.safetensors (deflated 8%)
  adding: content/llama-dialogue-summarizer/README.md (deflated 66%)
  adding: content/llama-dialogue-summarizer/tokenizer_config.json (deflated 67%)
  adding: content/llama-dialogue-summarizer/adapter_config.json (deflated 50%)


In [ ]:
from transformers import TextStreamer
model.config.use_cache = True
model.eval()

PeftModel(
  (base_model): LoraModel(
    (model): LlamaForCausalLM(
      (model): LlamaModel(
        (embed_tokens): Embedding(32000, 4096, padding_idx=0)
        (layers): ModuleList(
          (0-31): 32 x LlamaDecoderLayer(
            (self_attn): LlamaAttention(
              (q_proj): lora.Linear4bit(
                (base_layer): Linear4bit(in_features=4096, out_features=4096, bias=False)
                (lora_dropout): ModuleDict(
                  (default): Dropout(p=0.1, inplace=False)
                )
                (lora_A): ModuleDict(
                  (default): Linear(in_features=4096, out_features=16, bias=False)
                )
                (lora_B): ModuleDict(
                  (default): Linear(in_features=16, out_features=4096, bias=False)
                )
                (lora_embedding_A): ParameterDict()
                (lora_embedding_B): ParameterDict()
              )
              (k_proj): lora.Linear4bit(
                (base_layer): Linear4b